In [1]:
import numpy as np
import cv2
from bs4 import BeautifulSoup
import os
import glob

In [14]:
dataPath = './VOCdevkit/VOC2012/' 
categoryPath = 'Annotations/'
imagePath = 'JPEGImages/'

In [17]:
years = ('2007', '2008', '2009', '2010', '2011', '2012')
endOfData = (9950, 8773, 5331, 6994, 7214, 4331)
filenumber = '0'
name = list()
xmin = list()
ymin = list()
xmax = list()
ymax = list()
a = list()
count = 0
img = list()
numberOfFile = 0

for i in range(len(years)):
    year = years[i]
    EOD = int(year)-2007
    print('Year = ',year)
    for currentDataNumber in range(endOfData[EOD]):
        if 0 <= currentDataNumber and currentDataNumber < 10 :
            filenumber = '00000'
        elif 10 <= currentDataNumber and currentDataNumber < 100 :
            filenumber = '0000'
        elif 100 <= currentDataNumber and currentDataNumber < 1000 :
            filenumber = '000'
        elif 1000 <= currentDataNumber and currentDataNumber < 10000 :
            filenumber = '00'

        filenumber = filenumber + str(currentDataNumber)
        url_annotation = dataPath+categoryPath+str(year)+'_'+filenumber+'.xml'
        url_image = dataPath+imagePath+str(year)+'_'+filenumber+'.jpg'
        print(str(filenumber))

        try :
            ## for annotations ##
            xml = open(url_annotation, "r", encoding="utf-8").read()

            ## for images ##
            img = cv2.imread(url_image)
            numberOfFile += 1
            pass
        except :
            print("Image doesn't exist : " + filenumber)
            continue

        soup = BeautifulSoup(xml, 'html.parser')

        for size in soup.find_all('size'):
            width = size.find('width').string
            height = size.find('height').string
            depth = size.find('depth').string

        for object in soup.find_all('object'):
            name = object.find('name').string # edited
            for bndbox in object.find_all('bndbox'):
                xmin = object.find('xmin').string
                ymin = object.find('ymin').string
                xmax = object.find('xmax').string
                ymax = object.find('ymax').string

            # print('width : ' + width)
            # print('height : ' + height)
            # print('depth : ' + depth)
            #
            # print('label : ' + str(name))
            # print('xmin : ' + str(xmin))
            # print('ymin : ' + str(ymin))
            # print('xmax : ' + str(xmax))
            # print('ymax : ' + str(ymax))

            font = cv2.FONT_HERSHEY_SIMPLEX
            xmin = int(float(xmin))
            xmax = int(float(xmax))
            ymin = int(float(ymin))
            ymax = int(float(ymax))
            crop = img[int(ymin): int(ymax), int(xmin):int(xmax)]

            ## for one hot encoding ##
            if name == 'person':
                name = (1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'bird':
                name = (0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'cat':
                name = (0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'cow':
                name = (0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'dog':
                name = (0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'horse':
                name = (0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'sheep':
                name = (0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'aeroplane':
                name = (0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'bicycle':
                name = (0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0,0)
            elif name == 'boat':
                name = (0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0,0)
            elif name == 'bus':
                name = (0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0,0)
            elif name == 'car':
                name = (0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0,0)
            elif name == 'motorbike':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0,0)
            elif name == 'train':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0,0)
            elif name == 'bottle':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0,0)
            elif name == 'chair':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0,0)
            elif name == 'diningtable':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0,0)
            elif name == 'pottedplant':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0,0)
            elif name == 'sofa':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1,0)
            elif name == 'tvmonitor':
                name = (0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,0,1)

            file_name = 'pascal_voc_' + str(count)
#             crop = cv2.resize(crop, dsize=(224, 224))
            count += 1
            cv2.imwrite("./PascalDataSetCroppedEdited/" + file_name +'.jpg', crop)
            np.savetxt("./PascalDataSetCroppedEdited/" + file_name+'.txt', name , delimiter=' ', encoding='utf-8')

            print('from '+str(numberOfFile)+'th file '+str(count) + ' images have been successfully made !!')

Year =  2007
000000
Image doesn't exist : 000000
000001
Image doesn't exist : 000001
000002
Image doesn't exist : 000002
000003
Image doesn't exist : 000003
000004
Image doesn't exist : 000004
000005
Image doesn't exist : 000005
000006
Image doesn't exist : 000006
000007
Image doesn't exist : 000007
000008
Image doesn't exist : 000008
000009
Image doesn't exist : 000009
000010
Image doesn't exist : 000010
000011
Image doesn't exist : 000011
000012
Image doesn't exist : 000012
000013
Image doesn't exist : 000013
000014
Image doesn't exist : 000014
000015
Image doesn't exist : 000015
000016
Image doesn't exist : 000016
000017
Image doesn't exist : 000017
000018
Image doesn't exist : 000018
000019
Image doesn't exist : 000019
000020
Image doesn't exist : 000020
000021
Image doesn't exist : 000021
000022
Image doesn't exist : 000022
000023
Image doesn't exist : 000023
000024
Image doesn't exist : 000024
000025
Image doesn't exist : 000025
000026
Image doesn't exist : 000026
000027
from 1th

from 15th file 34 images have been successfully made !!
from 15th file 35 images have been successfully made !!
from 15th file 36 images have been successfully made !!
000242
Image doesn't exist : 000242
000243
from 16th file 37 images have been successfully made !!
000244
Image doesn't exist : 000244
000245
Image doesn't exist : 000245
000246
Image doesn't exist : 000246
000247
Image doesn't exist : 000247
000248
Image doesn't exist : 000248
000249
Image doesn't exist : 000249
000250
from 17th file 38 images have been successfully made !!
from 17th file 39 images have been successfully made !!
000251
Image doesn't exist : 000251
000252
Image doesn't exist : 000252
000253
Image doesn't exist : 000253
000254
Image doesn't exist : 000254
000255
Image doesn't exist : 000255
000256
from 18th file 40 images have been successfully made !!
000257
Image doesn't exist : 000257
000258
Image doesn't exist : 000258
000259
Image doesn't exist : 000259
000260
Image doesn't exist : 000260
000261
Imag

from 29th file 61 images have been successfully made !!
from 29th file 62 images have been successfully made !!
000465
Image doesn't exist : 000465
000466
Image doesn't exist : 000466
000467
Image doesn't exist : 000467
000468
Image doesn't exist : 000468
000469
Image doesn't exist : 000469
000470
Image doesn't exist : 000470
000471
Image doesn't exist : 000471
000472
Image doesn't exist : 000472
000473
Image doesn't exist : 000473
000474
Image doesn't exist : 000474
000475
Image doesn't exist : 000475
000476
Image doesn't exist : 000476
000477
Image doesn't exist : 000477
000478
Image doesn't exist : 000478
000479
Image doesn't exist : 000479
000480
from 30th file 63 images have been successfully made !!
from 30th file 64 images have been successfully made !!
from 30th file 65 images have been successfully made !!
from 30th file 66 images have been successfully made !!
000481
Image doesn't exist : 000481
000482
Image doesn't exist : 000482
000483
Image doesn't exist : 000483
000484
Im

from 44th file 98 images have been successfully made !!
from 44th file 99 images have been successfully made !!
from 44th file 100 images have been successfully made !!
000662
Image doesn't exist : 000662
000663
from 45th file 101 images have been successfully made !!
from 45th file 102 images have been successfully made !!
from 45th file 103 images have been successfully made !!
from 45th file 104 images have been successfully made !!
from 45th file 105 images have been successfully made !!
from 45th file 106 images have been successfully made !!
000664
from 46th file 107 images have been successfully made !!
000665
Image doesn't exist : 000665
000666
Image doesn't exist : 000666
000667
Image doesn't exist : 000667
000668
Image doesn't exist : 000668
000669
Image doesn't exist : 000669
000670
Image doesn't exist : 000670
000671
Image doesn't exist : 000671
000672
Image doesn't exist : 000672
000673
Image doesn't exist : 000673
000674
Image doesn't exist : 000674
000675
Image doesn't e

from 60th file 151 images have been successfully made !!
from 60th file 152 images have been successfully made !!
000823
Image doesn't exist : 000823
000824
Image doesn't exist : 000824
000825
Image doesn't exist : 000825
000826
Image doesn't exist : 000826
000827
Image doesn't exist : 000827
000828
Image doesn't exist : 000828
000829
Image doesn't exist : 000829
000830
from 61th file 153 images have been successfully made !!
from 61th file 154 images have been successfully made !!
from 61th file 155 images have been successfully made !!
from 61th file 156 images have been successfully made !!
000831
Image doesn't exist : 000831
000832
Image doesn't exist : 000832
000833
Image doesn't exist : 000833
000834
Image doesn't exist : 000834
000835
Image doesn't exist : 000835
000836
from 62th file 157 images have been successfully made !!
from 62th file 158 images have been successfully made !!
000837
from 63th file 159 images have been successfully made !!
000838
Image doesn't exist : 00083

...

from 16790th file 39699 images have been successfully made !!
from 16790th file 39700 images have been successfully made !!
from 16790th file 39701 images have been successfully made !!
003704
Image doesn't exist : 003704
003705
from 16791th file 39702 images have been successfully made !!
003706
from 16792th file 39703 images have been successfully made !!
003707
from 16793th file 39704 images have been successfully made !!
003708
from 16794th file 39705 images have been successfully made !!
003709
from 16795th file 39706 images have been successfully made !!
003710
Image doesn't exist : 003710
003711
Image doesn't exist : 003711
003712
Image doesn't exist : 003712
003713
Image doesn't exist : 003713
003714
from 16796th file 39707 images have been successfully made !!
003715
from 16797th file 39708 images have been successfully made !!
003716
from 16798th file 39709 images have been successfully made !!
003717
Image doesn't exist : 003717
003718
Image doesn't exist : 003718
003719
fro

Image doesn't exist : 003840
003841
from 16854th file 39782 images have been successfully made !!
003842
from 16855th file 39783 images have been successfully made !!
003843
from 16856th file 39784 images have been successfully made !!
003844
Image doesn't exist : 003844
003845
from 16857th file 39785 images have been successfully made !!
003846
from 16858th file 39786 images have been successfully made !!
003847
Image doesn't exist : 003847
003848
from 16859th file 39787 images have been successfully made !!
003849
from 16860th file 39788 images have been successfully made !!
003850
Image doesn't exist : 003850
003851
from 16861th file 39789 images have been successfully made !!
from 16861th file 39790 images have been successfully made !!
from 16861th file 39791 images have been successfully made !!
003852
from 16862th file 39792 images have been successfully made !!
003853
from 16863th file 39793 images have been successfully made !!
003854
Image doesn't exist : 003854
003855
from 1

from 16923th file 39869 images have been successfully made !!
003984
Image doesn't exist : 003984
003985
from 16924th file 39870 images have been successfully made !!
003986
from 16925th file 39871 images have been successfully made !!
003987
from 16926th file 39872 images have been successfully made !!
from 16926th file 39873 images have been successfully made !!
from 16926th file 39874 images have been successfully made !!
003988
from 16927th file 39875 images have been successfully made !!
003989
Image doesn't exist : 003989
003990
from 16928th file 39876 images have been successfully made !!
from 16928th file 39877 images have been successfully made !!
from 16928th file 39878 images have been successfully made !!
003991
from 16929th file 39879 images have been successfully made !!
from 16929th file 39880 images have been successfully made !!
003992
from 16930th file 39881 images have been successfully made !!
003993
Image doesn't exist : 003993
003994
from 16931th file 39882 images

from 16994th file 39969 images have been successfully made !!
004099
from 16995th file 39970 images have been successfully made !!
004100
Image doesn't exist : 004100
004101
from 16996th file 39971 images have been successfully made !!
004102
from 16997th file 39972 images have been successfully made !!
from 16997th file 39973 images have been successfully made !!
004103
from 16998th file 39974 images have been successfully made !!
004104
from 16999th file 39975 images have been successfully made !!
004105
Image doesn't exist : 004105
004106
from 17000th file 39976 images have been successfully made !!
004107
from 17001th file 39977 images have been successfully made !!
004108
Image doesn't exist : 004108
004109
from 17002th file 39978 images have been successfully made !!
from 17002th file 39979 images have been successfully made !!
004110
Image doesn't exist : 004110
004111
from 17003th file 39980 images have been successfully made !!
004112
from 17004th file 39981 images have been s

from 17069th file 40060 images have been successfully made !!
004232
from 17070th file 40061 images have been successfully made !!
004233
Image doesn't exist : 004233
004234
Image doesn't exist : 004234
004235
Image doesn't exist : 004235
004236
Image doesn't exist : 004236
004237
Image doesn't exist : 004237
004238
from 17071th file 40062 images have been successfully made !!
004239
from 17072th file 40063 images have been successfully made !!
004240
Image doesn't exist : 004240
004241
from 17073th file 40064 images have been successfully made !!
004242
Image doesn't exist : 004242
004243
Image doesn't exist : 004243
004244
from 17074th file 40065 images have been successfully made !!
004245
from 17075th file 40066 images have been successfully made !!
from 17075th file 40067 images have been successfully made !!
from 17075th file 40068 images have been successfully made !!
004246
from 17076th file 40069 images have been successfully made !!
004247
from 17077th file 40070 images have 